## Goodreads Text Features

I'm aware this is the most in-efficient code to ever be bestowed upon this planet <sub>however idc</sub>.

Following cell sets up Spark so it can connect to the cloud storage account where the data lives.

In [ ]:
spark.conf.set(
  "fs.azure.account.key.goodreadsreviews60300832.dfs.core.windows.net",
  "dj khaledddddd anotha one"
)

NameError: name 'spark' is not defined

In [0]:

storage_acct = "goodreadsreviews60300832"   
container    = "lakehouse"

gold_path  = f"abfss://{container}@{storage_acct}.dfs.core.windows.net/gold"
train_path = f"{gold_path}/features_v2/train"  


In [0]:
from pyspark.sql import functions as F
from pyspark.sql import types as T
import re

try:    import nltk
except ModuleNotFoundError:
    pass

try:
    nltk.data.find("sentiment/vader_lexicon.zip")
except LookupError:
    nltk.download("vader_lexicon")

Added this function that loads data stored in Delta or Parquet format bc for some reason the delta table would be annoying and it wouldn'load.

In [0]:
# ============ 1) LOAD ============
def read_delta_or_parquet(path: str):
    try:
        return spark.read.format("delta").load(path)
    except Exception:
        return spark.read.format("parquet").load(path)

train = read_delta_or_parquet(train_path)
train.printSchema()
display(train.select("review_id","review_text").limit(10))

root
 |-- review_id: string (nullable = true)
 |-- user_id: string (nullable = true)
 |-- book_id: string (nullable = true)
 |-- author_id: string (nullable = true)
 |-- author_name: string (nullable = true)
 |-- title: string (nullable = true)
 |-- language_code: string (nullable = true)
 |-- n_votes: long (nullable = true)
 |-- rating: double (nullable = true)
 |-- review_text: string (nullable = true)
 |-- review_length_words: integer (nullable = true)
 |-- review_length_chars: integer (nullable = true)
 |-- date_added: date (nullable = true)
 |-- book_review_count: long (nullable = true)
 |-- book_avg_rating: double (nullable = true)



review_id review_text 000197dca1e705ed3a3e7be5494e41c7 this has to be one of my all time favourite reads, i think it such a passionate and a haunting book. an old teacher and i would spend ages arguing about it as i thought it was so romantic and he would disagree but i stand by it! it has one of the most beautiful lines i've ever read 'i love everything about her, the air above her head and the ground beneath her feet...(or words to that effect) heathcliff and cathy loved each other so much it destroyed them, they loved each other in this world and the next....ok when you put it like that he had a point! a great book with some legendary characters. 000250b46f177fe76441bbd178a64671 amazing graphics. and very cool to read a part of the story i never knew about before. also made more palatable by the lack of king's involvement. i'm still pissed at him. 00027dd587d48a1ea0799f140b0fef60 una biografia escrita como si fuera un bonito paseo por la vida del autor. una manera de ver a traves de los ojos del otro el comienzo dr una etapa y el fin de muchas otras. me gusto el libro. 00064c6ed6be9052c383a5f8a26d1cf9 susanna kearsley knocks us off our feet with her spectacular tale of love overcoming all obstacles in her wondrous time travel romance, the rose garden . mourning the death of her beloved sister, eva returns to cornwall to scatter her ashes at the estate where they spent their happiest childhood summers. the people and the countryside are as she remembers--but not quite. voices speak from empty rooms, paths appear in places where none exist, and a handsome man dressed in breeches and boots beckons her to another time. daniel doesn't know what to make of the beautiful woman wearing strange clothes who appears on the hillside beside him. 1715 england is a dangerous place, with the jacobites threatening the reign of the newly crowned george i. is she involved in the upcoming confrontation between the supporters of george i and those of james stuart, whom some consider the rightful king? the rose garden is a masterwork of suspenseful romance. with vivid descriptions of the unchanging atlantic and its salt spray, the green of the hilly cornwall estate's rose gardens, and faithful renditions of the tensions and way of life of two very different eras, ms. kearsley melds past and present into a coherent whole that firmly anchors the reader into each time period. we live eva's confusion, disbelief and terror as she fades in and out of a past where danger lurks at every turn. both eva and daniel are people of their eras, but unique enough to accept something as outlandish as time travel, and to love a person of extraordinary background. daniel is as forceful as any eighteenth century man, but he also possesses the sensitivity a modern woman appreciates. and while eva has plenty of twenty-first century backbone, she is smart enough to adapt to the harsh conditions in 1715 without betraying herself. the romance is breath-taking, as eva and daniel, stronger together than singly, seek to triumph over villains and situations that would have destroyed lesser souls. and ms. kearsley leaves us gasping at the end with a corker of a surprise. read the rose garden . you'll be happy you did. arc provided by sourcebooks 000671601b00cc04bd8eaf95de8f1ab4 my copy, provided by the author in exchange for an honest review, is for the second edition from rocky ridge books. nice presentation, btw. this second book in the dark angels series is an excellent second look at the band and all its gay members. josh and robin showed up in the first book as supporting characters to larger than life angel and his waffling bisexual love interest dare. we could see clearly from their brief moments in the first book that there are issues. a huge theme is "who is family?" and "what does that mean?" the band's prurient audiences love the idea of twincest, (which for me is automatic back button) but the guys are stepbrothers. it's a close enough connection to keep things f

Make stuff lowercase, removing extra symbols, etc. so it’s easier to work with -- some basic cleaning

In [0]:
# ============ 2) TEXT CLEANING & NORMALIZATION ============

url_re   = re.compile(r"(https?://\S+|www\.\S+)", flags=re.IGNORECASE)
num_re   = re.compile(r"\b\d+([.,]\d+)*\b")
punc_re  = re.compile(r"[^\w\s]", flags=re.UNICODE)
space_re = re.compile(r"\s+")

emoji_re = re.compile(
    "[\U0001F300-\U0001F6FF\U0001F900-\U0001FAFF\U00002700-\U000027BF\U00002600-\U000026FF]"
)

@F.udf(returnType=T.StringType())
def clean_text_u(text):
    if text is None:
        return None
    s = text.strip().lower()
    s = url_re.sub(" <URL> ", s)
    s = num_re.sub(" <NUM> ", s)
    s = emoji_re.sub(" <EMOJI> ", s)
    s = punc_re.sub(" ", s)        
    s = space_re.sub(" ", s).strip() 
    return s

cleaned = (
    train
    .withColumn("clean_text", clean_text_u(F.col("review_text")))
    .withColumn("_len_chars", F.length("clean_text"))
    .filter(F.col("_len_chars") >= 10)   
    .drop("_len_chars")
)

display(cleaned.select("review_id","clean_text").limit(10))

review_id clean_text 000118172d28cf5a070fe4c3c5272959 this extraordinary novel centering on lilith born into slavery on a jamaica plantation in the late 18th century deals with the dehumanizing effect of slavery on both the slaveholders and the enslaved it s moral complex and emotionally challenging to read the characters are damaged and very very real james writes in dialect effectively by capturing the rhythm and word usage highest recommendation 0001eb3b3b31e2c5b7853b2449114f99 i voluntarily received an advance reader copy of this book this story definitely takes a reader for a walk on the dark side of romance there is so much forbidden about this story that it is impossible to put it down you just have to know what is going to happen next his muse is one may december romance that is not for the faint of heart but the happily ever after made all the drama and suspense worth while 00048c0e175f115459d66d4bc26bf9a3 this was a super quick read which is actually beneficial if you re interested in a brief overview regarding the maori and the british crown esp the treaty of waitangi then this book has a lot of simple and quick information to pick up you won t end up being an expert but you can learn what you need here the writing is not only informative but is actually quite upbeat and it was a pleasant read no droll scholarship here great writing good information and something i would recommend 00072889d415fffaa40ebb31c46163cc i so thought i would of given this NUM stars just because there was not enough of edward in this book but i couldn t help myself it gets NUM awesome stars i m officially addicted to edward and bella i so want her to become part of the cullen family NUM its a shame these books sat on my bookshelf for so many years 0007d67628b02f7731c73e6f683dbe08 i had no sooner finished reading embattled minds the book i last reviewed when i started reading this one i was so taken with the first book by this author by her writing by her realness by the characters by the concept that i had no choice but to read the first book in the series this is the story of john palmer and shannon murphy john is one of founders of lost n found investigative agency a detective agency organized and run by wounded vets john is quite the gruff unfriendly kind of guy he was paralyzed from an injury but yes he can wink and has become even more unsociable since being stuck in a wheel chair his past is a sad and lonely one so the reader can see why he is the way he is shannon has recently been hired by the agency as the office manager from the beginning they notice each other but because each has quite a set of baggage they don t act on any attraction they may have that is until john notices that shannon seems off and wants to know why it turns out that something has gone terribly wrong she had a very scary stalker years ago but he is in prison now yet many of the same things are starting to happen that he did years ago a pepsi can left where she can t help but see it and it has the stalkers finger prints yet he is in jail john takes no time in moving in with her to protect her and get the rest of agency on the case this one didn t get to me quite as much as embattled minds while the previous is a NUM this one would be a NUM NUM NUM if we could give NUM NUM marks i love a gruff teddy bear type of hero but i didn t find john teddy bearish he is reluctant to believe that shannon could really be interested in him at all he was often rude and while i could understand why he is the way he is he just doesn t have that inner marshmallow that makes this kind of hero so attractive i like shannon though she isn t a real stand out kind of heroine i did appreciate how calm and collected she remained despite the threat she is under and i also liked how she wasn t bothered at all by john s infirmity she wants him she goes after him that simple like the first one i read embattled hearts this one is also novella size in length but again like the first one i foun

This part adds two basic text features to the data:
- how many characters are in the cleaned review
- how many words are in the cleaned review

In [0]:
# ============ 3) BASIC TEXT FEATURES ============
with_basic = (
    cleaned
    .withColumn("review_length_chars", F.length("clean_text").cast("int"))
    .withColumn("review_length_words",
                F.size(F.split(F.col("clean_text"), r"\s+")).cast("int"))
)

display(with_basic.select("review_id","review_length_words","review_length_chars").limit(10))

review_id review_length_words review_length_chars 000118172d28cf5a070fe4c3c5272959 63 398 0001eb3b3b31e2c5b7853b2449114f99 80 409 00048c0e175f115459d66d4bc26bf9a3 90 485 00072889d415fffaa40ebb31c46163cc 65 314 0007d67628b02f7731c73e6f683dbe08 551 2720 000819bbe58c374dfb956abe6238f30c 220 1169 00085ae1bfa285138f710e5009c79381 45 214 000aa569b4f3aeb75312edd7f7d3c8f2 253 1386 000c29d5198b932bfd167ce9ca31c611 39 200 000dd791f3d4868b490d65e69b0eaa85 54 309

This section calculates sentiment scores for each review using the VADER sentiment tool.
It creates four values:
- pos → how positive the review is
- neu → how neutral it is
- neg → how negative it is

compound is the overall sentiment score from -1 (very negative) to +1 (very positive)

In [0]:
from pyspark.sql import functions as F, types as T

# ============ 4) SENTIMENT (vaderSentiment) ============
@F.udf(returnType=T.StructType([
    T.StructField("pos", T.DoubleType(), True),
    T.StructField("neu", T.DoubleType(), True),
    T.StructField("neg", T.DoubleType(), True),
    T.StructField("compound", T.DoubleType(), True),
]))
def vader_scores_u(text):
    if text is None or text == "":
        return (0.0, 1.0, 0.0, 0.0)
    from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
    sia = SentimentIntensityAnalyzer()
    s = sia.polarity_scores(text)
    return (float(s["pos"]), float(s["neu"]), float(s["neg"]), float(s["compound"]))

with_sent = (
    with_basic
    .withColumn("vader", vader_scores_u(F.col("clean_text")))
    .withColumn("sentiment_pos", F.col("vader.pos"))
    .withColumn("sentiment_neu", F.col("vader.neu"))
    .withColumn("sentiment_neg", F.col("vader.neg"))
    .withColumn("sentiment_compound", F.col("vader.compound"))
    .drop("vader")
)

display(with_sent.select("review_id","sentiment_pos","sentiment_neu","sentiment_neg","sentiment_compound").limit(10))


review_id sentiment_pos sentiment_neu sentiment_neg sentiment_compound 000118172d28cf5a070fe4c3c5272959 0.085 0.684 0.231 -0.93 0001eb3b3b31e2c5b7853b2449114f99 0.178 0.799 0.022 0.9226 00048c0e175f115459d66d4bc26bf9a3 0.235 0.739 0.026 0.9719 00072889d415fffaa40ebb31c46163cc 0.148 0.798 0.054 0.7999 0007d67628b02f7731c73e6f683dbe08 0.132 0.774 0.094 0.9814 000819bbe58c374dfb956abe6238f30c 0.097 0.76 0.142 -0.8979 00085ae1bfa285138f710e5009c79381 0.226 0.774 0.0 0.9001 000aa569b4f3aeb75312edd7f7d3c8f2 0.126 0.845 0.029 0.9666 000c29d5198b932bfd167ce9ca31c611 0.157 0.843 0.0 0.7845 000dd791f3d4868b490d65e69b0eaa85 0.3 0.656 0.044 0.9559

This part builds TF–IDF features manually in Spark (without using Spark MLlib):
- First, it splits each review into words and saves them as tokens.
- Then it removes common words (like “the”, “and”, “of”) using a stopword list.
- It also creates bigrams (pairs of words like "very good") and combines them with single words.
- Next, it counts how many documents each term appears in to get document frequency (DF).
- It keeps the most frequent terms as the vocabulary (up to 20,000 terms).
- It then computes IDF for each term and builds a TF–IDF vector for every review.
- The final result is a tfidf_features column, which is a numeric vector that models can use as input.

I just hard-coded my own stopword list because the library version kept breaking in my environment. Spark kept throwing weird errors, so this way actually worked and i did wanna change it later but aint no way im running this for 2 hours again.

In [0]:
# =================== 5) TF–IDF in pure Spark (no MLlib, no broadcasts) ===================
from pyspark.sql import functions as F, types as T
from pyspark.ml.linalg import Vectors, VectorUDT
import math, numpy as np

# 5.1 Tokenize via SQL split (whitespace)
df_tok = with_sent.withColumn("tokens", F.split(F.col("clean_text"), r"\s+"))

# 5.2 Stopword removal via UDF (STOPWORDS captured as a constant, not broadcast)
STOPWORDS = {
    "a","about","above","after","again","against","all","am","an","and","any","are","as","at",
    "be","because","been","before","being","below","between","both","but","by",
    "can","could",
    "did","do","does","doing","down","during",
    "each","few","for","from","further",
    "had","has","have","having","he","her","here","hers","herself","him","himself","his","how",
    "i","if","in","into","is","it","its","itself",
    "just",
    "me","more","most","my","myself",
    "no","nor","not","now",
    "of","off","on","once","only","or","other","our","ours","ourselves","out","over","own",
    "same","she","should","so","some","such",
    "than","that","the","their","theirs","them","themselves","then","there","these","they",
    "this","those","through","to","too",
    "under","until","up",
    "very",
    "was","we","were","what","when","where","which","while","who","whom","why","will","with",
    "you","your","yours","yourself","yourselves"
}

@F.udf(returnType=T.ArrayType(T.StringType()))
def remove_stop_u(tokens):
    if tokens is None:
        return []
    return [t for t in tokens if t and (t not in STOPWORDS)]

df_sw = df_tok.withColumn("tokens_sw", remove_stop_u(F.col("tokens")))

# 5.3 Bigrams in SQL (adjacent pairs)
@F.udf(returnType=T.ArrayType(T.StringType()))
def bigrams_u(tokens):
    if not tokens:
        return []
    n = len(tokens)
    if n < 2:
        return []
    return [tokens[i] + " " + tokens[i+1] for i in range(n-1)]

df_bg = df_sw.withColumn("bigrams", bigrams_u(F.col("tokens_sw")))

# 5.4 Combine unigrams + bigrams
df_grams = df_bg.withColumn("tokens_all", F.concat(F.col("tokens_sw"), F.col("bigrams")))

# 5.5 Document frequency (DF) per term in Spark; filter minDF>=5
expl = (df_grams
        .select("review_id", F.explode_outer("tokens_all").alias("term"))
        .dropna(subset=["term"])
        .dropDuplicates(["review_id","term"])
       )

N_docs = df_grams.select(F.countDistinct("review_id").alias("N")).collect()[0]["N"]
df_df = (expl.groupBy("term")
              .agg(F.count("*").alias("df"))
              .filter(F.col("df") >= 5))

# 5.6 Vocabulary (top DF terms up to MAX_FEATURES)
MAX_FEATURES = 20000
vocab_rows = (df_df.orderBy(F.desc("df"))
                   .limit(MAX_FEATURES)
                   .collect())

# Build global vocab + idf **without** broadcast; UDFs will capture these globals
VOCAB_LIST  = [r["term"] for r in vocab_rows]
VOCAB_INDEX = {t: i for i, t in enumerate(VOCAB_LIST)}

IDF_VEC = np.zeros(len(VOCAB_LIST), dtype="float32")
df_map  = {r["term"]: r["df"] for r in vocab_rows}
for term, idx in VOCAB_INDEX.items():
    df_term = df_map.get(term, 0)
    # sklearn-style idf
    IDF_VEC[idx] = math.log((N_docs + 1.0) / (df_term + 1.0)) + 1.0
IDF_VEC = IDF_VEC.tolist()  # make it JSON-serializable for the UDF

# 5.7 Build TF–IDF SparseVector via scalar UDF (captures VOCAB_INDEX & IDF_VEC)
@F.udf(returnType=VectorUDT())
def tfidf_from_tokens(tokens_all):
    vocab = VOCAB_INDEX
    idf   = IDF_VEC
    if not tokens_all:
        return Vectors.sparse(len(idf), [], [])
    tf = {}
    for t in tokens_all:
        idx = vocab.get(t)
        if idx is not None:
            tf[idx] = tf.get(idx, 0) + 1
    if not tf:
        return Vectors.sparse(len(idf), [], [])
    idxs = sorted(tf.keys())
    vals = [tf[i] * idf[i] for i in idxs]
    # L2 normalize
    norm = math.sqrt(sum(v*v for v in vals))
    if norm > 0:
        vals = [v / norm for v in vals]
    return Vectors.sparse(len(idf), idxs, vals)

with_tfidf = df_grams.withColumn("tfidf_features", tfidf_from_tokens(F.col("tokens_all")))
with_tfidf.select("review_id","tfidf_features").limit(1).printSchema()


root
 |-- review_id: string (nullable = true)
 |-- tfidf_features: vectorudt (nullable = true)



In [0]:
# --- 1) Inspect column list and schema ---
print("Column names →")
print(with_tfidf.columns)
print("\nSchema →")
with_tfidf.printSchema()

# --- 2) Show a sample of 10 rows with selected features ---
display(
    with_tfidf.select(
        "review_id",
        "clean_text",
        "review_length_words",
        "sentiment_compound",
        "tfidf_features"
    ).limit(10)
)


Column names →
['review_id', 'user_id', 'book_id', 'author_id', 'author_name', 'title', 'language_code', 'n_votes', 'rating', 'review_text', 'review_length_words', 'review_length_chars', 'date_added', 'book_review_count', 'book_avg_rating', 'clean_text', 'sentiment_pos', 'sentiment_neu', 'sentiment_neg', 'sentiment_compound', 'tokens', 'tokens_sw', 'bigrams', 'tokens_all', 'tfidf_features']

Schema →
root
 |-- review_id: string (nullable = true)
 |-- user_id: string (nullable = true)
 |-- book_id: string (nullable = true)
 |-- author_id: string (nullable = true)
 |-- author_name: string (nullable = true)
 |-- title: string (nullable = true)
 |-- language_code: string (nullable = true)
 |-- n_votes: long (nullable = true)
 |-- rating: double (nullable = true)
 |-- review_text: string (nullable = true)
 |-- review_length_words: integer (nullable = false)
 |-- review_length_chars: integer (nullable = true)
 |-- date_added: date (nullable = true)
 |-- book_review_count: long (nullable = tr

review_id clean_text review_length_words sentiment_compound tfidf_features 000118172d28cf5a070fe4c3c5272959 this extraordinary novel centering on lilith born into slavery on a jamaica plantation in the late 18th century deals with the dehumanizing effect of slavery on both the slaveholders and the enslaved it s moral complex and emotionally challenging to read the characters are damaged and very very real james writes in dialect effectively by capturing the rhythm and word usage highest recommendation 63 -0.93 Map(vectorType -> sparse, length -> 20000, indices -> List(1, 3, 10, 61, 113, 465, 610, 715, 759, 993, 1172, 1175, 1320, 1650, 1679, 1892, 2967, 3524, 3698, 3939, 4754, 5802, 5869, 5921, 6908, 7532, 9904, 13598, 14013, 15794), values -> List(0.04932970706592388, 0.05186490165864906, 0.06914555506243575, 0.09223831842048257, 0.10214211420969792, 0.13328630462895785, 0.13963342520552474, 0.14374470644837106, 0.14510381759293095, 0.15208747605810158, 0.1569790431498257, 0.15702907566019236, 0.16055810652765798, 0.16681385651657263, 0.16711755569877193, 0.17074422768441494, 0.18308293239144924, 0.1877963162985448, 0.18923448091722536, 0.19098427509494584, 0.39277538800172146, 0.20204040601530082, 0.20248570589627082, 0.20277781250102866, 0.20721355417840126, 0.20962266302472127, 0.21778038611704248, 0.22663928889058702, 0.22750580770756912, 0.23095475757700448)) 0001eb3b3b31e2c5b7853b2449114f99 i voluntarily received an advance reader copy of this book this story definitely takes a reader for a walk on the dark side of romance there is so much forbidden about this story that it is impossible to put it down you just have to know what is going to happen next his muse is one may december romance that is not for the faint of heart but the happily ever after made all the drama and suspense worth while 80 0.9226 Map(vectorType -> sparse, length -> 20000, indices -> List(0, 4, 5, 13, 29, 47, 51, 67, 94, 100, 106, 107, 138, 142, 154, 198, 229, 257, 276, 277, 284, 304, 519, 593, 804, 1266, 1388, 1468, 1817, 2226, 2311, 2457, 2931, 3508, 3617, 3960, 6006, 6205, 6518, 7534, 8856, 10784, 11553, 12045, 12869, 14283, 16926), values -> List(0.039120737265257575, 0.10500280686251472, 0.05294648394851563, 0.06575914674703631, 0.0738249485620122, 0.0809469650399376, 0.08174083630948559, 0.08440352407252882, 0.09085893149754987, 0.09142831964220927, 0.1839491449155402, 0.09204372178377809, 0.09721125061791108, 0.19494153004828224, 0.09835785806093922, 0.10313603172158697, 0.10648362311536926, 0.10931740248658622, 0.11020471040260196, 0.1102545743188273, 0.11098435189284886, 0.11229978277453127, 0.12305020197048336, 0.1256269499842074, 0.13276754157672382, 0.14430271161320876, 0.1467265133749148, 0.1480231662005229, 0.15354226727904052, 0.15882051263005934, 0.15978695578683585, 0.1613968308853481, 0.1655830242391491, 0.1700849229145914, 0.17081412747736593, 0.1731453879226777, 0.18411886368426797, 0.18487800808469945, 0.1861973067922993, 0.18996411560195073, 0.1942538688009169, 0.19943101348003903, 0.20121244575836322, 0.2022952937624257, 0.20392734917129146, 0.20668730559351692, 0.21106047967986227)) 00048c0e175f115459d66d4bc26bf9a3 this was a super quick read which is actually beneficial if you re interested in a brief overview regarding the maori and the british crown esp the treaty of waitangi then this book has a lot of simple and quick information to pick up you won t end up being an expert but you can learn what you need here the writing is not only informative but is actually quite upbeat and it was a pleasant read no droll scholarship here great writing good information and something i would recommend 90 0.9719 Map(vectorType -> sparse, length -> 20000, indices -> List(0, 2, 3, 11, 12, 24, 33, 56, 59, 64, 98, 109, 112, 122, 143, 246, 314, 315, 329, 372, 434, 507, 514, 597, 764, 918, 1585, 1712, 2160, 2161, 2406, 2767, 4365, 4876, 5003, 5169, 5607, 6299, 6542, 9606, 10050, 11159, 15420, 15823, 18997, 19377, 19837), values -> List(0.0371

In [0]:
# Drop intermediate text-processing columns
final_tfidf = (
    with_tfidf
    .drop("tokens", "tokens_sw", "bigrams", "tokens_all") 
)

print("Final columns →", final_tfidf.columns)
final_tfidf.printSchema()


Final columns → ['review_id', 'user_id', 'book_id', 'author_id', 'author_name', 'title', 'language_code', 'n_votes', 'rating', 'review_text', 'review_length_words', 'review_length_chars', 'date_added', 'book_review_count', 'book_avg_rating', 'clean_text', 'sentiment_pos', 'sentiment_neu', 'sentiment_neg', 'sentiment_compound', 'tfidf_features']
root
 |-- review_id: string (nullable = true)
 |-- user_id: string (nullable = true)
 |-- book_id: string (nullable = true)
 |-- author_id: string (nullable = true)
 |-- author_name: string (nullable = true)
 |-- title: string (nullable = true)
 |-- language_code: string (nullable = true)
 |-- n_votes: long (nullable = true)
 |-- rating: double (nullable = true)
 |-- review_text: string (nullable = true)
 |-- review_length_words: integer (nullable = false)
 |-- review_length_chars: integer (nullable = true)
 |-- date_added: date (nullable = true)
 |-- book_review_count: long (nullable = true)
 |-- book_avg_rating: double (nullable = true)
 |-- c

This chunk uses SBERT (a pre-trained language model) to turn each review into a numeric vector that captures its meaning.  
It does this in a memory-friendly way (small batches, sharded writes, local cache), then joins these embeddings with your TF-IDF features and saves the final combined feature table. I'm very aware this could have been so much better,<sub> once again, idc</sub>

In [0]:

# SBERT embeddings 

from typing import Iterator
import os, errno
import pandas as pd

from pyspark.sql import functions as F
from pyspark.sql.types import ArrayType, FloatType
from pyspark.sql.functions import pandas_udf, PandasUDFType

spark.conf.set("spark.sql.execution.arrow.pyspark.enabled", "true")
spark.conf.set("spark.sql.execution.arrow.maxRecordsPerBatch", "128")   
spark.conf.set("spark.sql.shuffle.partitions", "200")                  

# The clusters was blocking certain paths?? like so this tries a couple and uses whichever works idk
def _pick_cache_dir():
    for d in ["/tmp/hf_cache", "/var/tmp/hf_cache"]:
        try:
            os.makedirs(d, exist_ok=True)
            testfile = os.path.join(d, ".touch")
            with open(testfile, "w") as f:
                f.write("ok")
            os.remove(testfile)
            return d
        except OSError as e:
            if e.errno not in (errno.EACCES, errno.EROFS):
                raise
    raise OSError("No writable cache dir available (tried /tmp and /var/tmp).")

# This UDF takes batches of text and returns SBERT embeddings.
# I used the iterator version so Spark doesn't try to load everything at once and cause the OOM error again
@pandas_udf(ArrayType(FloatType()), PandasUDFType.SCALAR_ITER)
def sbert_embed_iter(batch_iter: Iterator[pd.Series]) -> Iterator[pd.Series]:
    cache_dir = _pick_cache_dir()
    os.environ["HF_HOME"] = cache_dir
    os.environ["TRANSFORMERS_CACHE"] = cache_dir
    os.environ["SENTENCE_TRANSFORMERS_HOME"] = cache_dir
    os.environ["TOKENIZERS_PARALLELISM"] = "false"

    global _sbert_model
    if "_sbert_model" not in globals():
        from sentence_transformers import SentenceTransformer
        _sbert_model = SentenceTransformer(
            "sentence-transformers/all-MiniLM-L6-v2",
            cache_folder=cache_dir,
        )
        _sbert_model.max_seq_length = 256

    for s in batch_iter:
        arr = s.fillna("").astype(str)
        embs = _sbert_model.encode(
            arr.tolist(),
            batch_size=32,                  
            normalize_embeddings=True,
            show_progress_bar=False,
        )
        yield pd.Series([list(map(float, e)) for e in embs])

# I kept only the columns needed for SBERT (review_id + text)
text_df = with_sent.select("review_id", "clean_text").repartition(200)
text_df = text_df.persist()


emb_out = f"{gold_path}/features_v2/train_text_embeddings_sbert"
# Clean target once
spark.sql(f"DROP TABLE IF EXISTS delta.`{emb_out}`")  

# I used sharding (50 splits) to avoid doing one massive job that might OOM.
# Each shard runs independently and appends its results.
SHARDS = 50  
for i in range(SHARDS):
    part = (text_df
            .where(F.pmod(F.hash("review_id"), F.lit(SHARDS)) == F.lit(i))
            .withColumn("bert_embedding", sbert_embed_iter(F.col("clean_text")))
            .select("review_id", "bert_embedding"))
    (part.write.format("delta")
         .mode("append")        
         .save(emb_out))

text_df.unpersist()

# Load embeddings 
emb_df = spark.read.format("delta").load(emb_out)
emb_df.select(F.size("bert_embedding").alias("dim")).limit(5).show()

train_all = (
    final_tfidf
    .join(emb_df, on="review_id", how="inner")
)

train_all_out = f"{gold_path}/features_v2/train_allfeatures"
(train_all.write.format("delta").mode("overwrite").save(train_all_out))

print(train_all_out)
train_all.printSchema()

/databricks/spark/python/pyspark/sql/pandas/functions.py:443: UserWarning: In Python 3.6+ and Spark 3.0+, it is preferred to specify type hints for pandas UDF instead of specifying pandas UDF type which will be deprecated in the future releases. See SPARK-28264 for more details.
  warnings.warn(


+---+
|dim|
+---+
|384|
|384|
|384|
|384|
|384|
+---+

abfss://lakehouse@goodreadsreviews60300832.dfs.core.windows.net/gold/features_v2/train_allfeatures
root
 |-- review_id: string (nullable = true)
 |-- user_id: string (nullable = true)
 |-- book_id: string (nullable = true)
 |-- author_id: string (nullable = true)
 |-- author_name: string (nullable = true)
 |-- title: string (nullable = true)
 |-- language_code: string (nullable = true)
 |-- n_votes: long (nullable = true)
 |-- rating: double (nullable = true)
 |-- review_text: string (nullable = true)
 |-- review_length_words: integer (nullable = false)
 |-- review_length_chars: integer (nullable = true)
 |-- date_added: date (nullable = true)
 |-- book_review_count: long (nullable = true)
 |-- book_avg_rating: double (nullable = true)
 |-- clean_text: string (nullable = true)
 |-- sentiment_pos: double (nullable = true)
 |-- sentiment_neu: double (nullable = true)
 |-- sentiment_neg: double (nullable = true)
 |-- sentiment_compoun

In [0]:
print(final_tfidf.count(), emb_df.count(), train_all.count())

9491109 9491109 9491109


In [0]:
display(
    spark.read.format("delta").load(train_all_out)
        .select(
            "review_id",
            "clean_text",
            "review_length_words",
            "sentiment_compound",
            "tfidf_features",
            "bert_embedding"
        )
        .limit(10)
)



review_id clean_text review_length_words sentiment_compound tfidf_features bert_embedding 000197dca1e705ed3a3e7be5494e41c7 this has to be one of my all time favourite reads i think it such a passionate and a haunting book an old teacher and i would spend ages arguing about it as i thought it was so romantic and he would disagree but i stand by it it has one of the most beautiful lines i ve ever read i love everything about her the air above her head and the ground beneath her feet or words to that effect heathcliff and cathy loved each other so much it destroyed them they loved each other in this world and the next ok when you put it like that he had a point a great book with some legendary characters 120 0.9851 Map(vectorType -> sparse, length -> 20000, indices -> List(0, 3, 5, 7, 9, 10, 12, 13, 15, 24, 27, 28, 46, 53, 67, 70, 100, 105, 107, 125, 134, 185, 266, 303, 482, 572, 605, 606, 701, 840, 863, 867, 1024, 1189, 1363, 1537, 1604, 1679, 1850, 2301, 2325, 2400, 2930, 3234, 3696, 3928, 4002, 5509, 8567, 9037, 11205, 16851, 19605, 19659), values -> List(0.07870877925998906, 0.04728074208570815, 0.10652542382930043, 0.057323266393540524, 0.06254571288474685, 0.06303401820361827, 0.1320100461769446, 0.06615189957365993, 0.06729409677090643, 0.07157556342699874, 0.07365115075013735, 0.14755772163546588, 0.08113023275471891, 0.08240083654350858, 0.08490763223536739, 0.08539190251895627, 0.0919743840720149, 0.09230542509165288, 0.09259346176204454, 0.09640984256569038, 0.09728991858700864, 0.10281208653827897, 0.1103299577213206, 0.11277412029854829, 0.12237225632330755, 0.12577776605659918, 0.12714240057831222, 0.12717602587233334, 0.1305216705732338, 0.13444397705756297, 0.13500762104859207, 0.1350785824280102, 0.13964609825943688, 0.1433979485211461, 0.14732513067310835, 0.1502714870165415, 0.1513295669380841, 0.15234661199188734, 0.1549123300070014, 0.16058647828273043, 0.1609261297794445, 0.16177299481840013, 0.1665690785859354, 0.1691754711977814, 0.17250501178465247, 0.17401077646898558, 0.17447654683634606, 0.18289540777268373, 0.1945639972587266, 0.19600182684010348, 0.20165561980391616, 0.21220051200894094, 0.2161310446812717, 0.21620405960543185)) List(-0.09395808, 0.020533582, 0.023684312, -0.0049843774, -0.045912594, 0.0052129235, 0.0075953025, -0.050689068, 0.044159897, 0.035144452, -0.025839988, 0.07185225, 0.107488826, -0.018397154, -0.015659777, 0.08869588, 0.0038001935, 0.018047577, 0.019914074, 0.039576318, -3.2426347E-4, 0.03845283, 0.049670022, 0.06432235, -0.06008428, -0.080892906, 0.05582591, 0.028310083, -0.090362184, -0.015064784, -0.066851325, -0.012716265, -0.033729102, -0.031012597, 0.0019423878, 0.0750589, 0.01450563, -0.021095097, 0.022074543, 0.0014487508, -0.0042560436, 0.03301075, 0.019492188, 0.006087645, -0.021252045, -0.037356433, -0.012903627, -0.06849498, -0.029681358, -0.013638408, 0.0086266175, 0.030276239, -0.13084114, -0.07070397, -0.008443375, 0.086747505, -0.012094665, -0.04219049, -0.006832875, -0.02894327, -0.05139066, -0.030714685, 0.015877882, 0.0218805, 0.006238747, 0.047494702, -0.07878259, -0.042115957, -0.040438756, -0.005822278, -0.14919136, 0.0072356802, 0.052921053, -0.048718676, 0.00672569, -0.022880388, -0.045975517, -0.16068529, -0.067957126, -0.014070602, -0.055086352, 0.001411571, 0.022028152, 0.024284968, 0.0022956475, -0.031728193, 0.039846435, -0.04041533, -0.03435686, -0.048912566, 0.032795053, -0.021275317, -0.07659051, 0.11468825, -0.04309492, 0.007669852, -0.04427864, -0.0038588592, -0.087742314, -0.036391787, 0.023017345, 0.10050072, -0.055710502, 0.050314594, 0.0083139455, -0.08866054, 0.0017466863, -0.04478916, -0.03689235, -0.045967154, 0.022819735, -0.056796312, -0.04754143, -0.018472891, 0.01481561, 0.036221292, 0.07763506, -0.05598234, 0.018530425, -0.040143996, -0.018669207, 0.059852753, 0.021760495, -0.020051988, 0.018513344, -0.1080032, 0.07960576, 2.2659764E-33, -0.029842075, 0.05672926, 0.008596384, 0.055128388, 0.06444329, -0.025806211, -0.0132951755,

In [0]:
display(
    spark.read.format("delta").load(f"{gold_path}/features_v2/train_allfeatures").limit(10)
)


review_id user_id book_id author_id author_name title language_code n_votes rating review_text review_length_words review_length_chars date_added book_review_count book_avg_rating clean_text sentiment_pos sentiment_neu sentiment_neg sentiment_compound tfidf_features bert_embedding 000197dca1e705ed3a3e7be5494e41c7 1e5b241799d306b385fc41908b1c11e1 6185 4191 Emily Bronte Wuthering Heights eng 0 4.0 this has to be one of my all time favourite reads, i think it such a passionate and a haunting book. an old teacher and i would spend ages arguing about it as i thought it was so romantic and he would disagree but i stand by it! it has one of the most beautiful lines i've ever read 'i love everything about her, the air above her head and the ground beneath her feet...(or words to that effect) heathcliff and cathy loved each other so much it destroyed them, they loved each other in this world and the next....ok when you put it like that he had a point! a great book with some legendary characters. 120 587 2008-09-04 2559 3.5498241500586167 this has to be one of my all time favourite reads i think it such a passionate and a haunting book an old teacher and i would spend ages arguing about it as i thought it was so romantic and he would disagree but i stand by it it has one of the most beautiful lines i ve ever read i love everything about her the air above her head and the ground beneath her feet or words to that effect heathcliff and cathy loved each other so much it destroyed them they loved each other in this world and the next ok when you put it like that he had a point a great book with some legendary characters 0.241 0.694 0.065 0.9851 Map(vectorType -> sparse, length -> 20000, indices -> List(0, 3, 5, 7, 9, 10, 12, 13, 15, 24, 27, 28, 46, 53, 67, 70, 100, 105, 107, 125, 134, 185, 266, 303, 482, 572, 605, 606, 701, 840, 863, 867, 1024, 1189, 1363, 1537, 1604, 1679, 1850, 2301, 2325, 2400, 2930, 3234, 3696, 3928, 4002, 5509, 8567, 9037, 11205, 16851, 19605, 19659), values -> List(0.07870877925998906, 0.04728074208570815, 0.10652542382930043, 0.057323266393540524, 0.06254571288474685, 0.06303401820361827, 0.1320100461769446, 0.06615189957365993, 0.06729409677090643, 0.07157556342699874, 0.07365115075013735, 0.14755772163546588, 0.08113023275471891, 0.08240083654350858, 0.08490763223536739, 0.08539190251895627, 0.0919743840720149, 0.09230542509165288, 0.09259346176204454, 0.09640984256569038, 0.09728991858700864, 0.10281208653827897, 0.1103299577213206, 0.11277412029854829, 0.12237225632330755, 0.12577776605659918, 0.12714240057831222, 0.12717602587233334, 0.1305216705732338, 0.13444397705756297, 0.13500762104859207, 0.1350785824280102, 0.13964609825943688, 0.1433979485211461, 0.14732513067310835, 0.1502714870165415, 0.1513295669380841, 0.15234661199188734, 0.1549123300070014, 0.16058647828273043, 0.1609261297794445, 0.16177299481840013, 0.1665690785859354, 0.1691754711977814, 0.17250501178465247, 0.17401077646898558, 0.17447654683634606, 0.18289540777268373, 0.1945639972587266, 0.19600182684010348, 0.20165561980391616, 0.21220051200894094, 0.2161310446812717, 0.21620405960543185)) List(-0.09395808, 0.020533582, 0.023684312, -0.0049843774, -0.045912594, 0.0052129235, 0.0075953025, -0.050689068, 0.044159897, 0.035144452, -0.025839988, 0.07185225, 0.107488826, -0.018397154, -0.015659777, 0.08869588, 0.0038001935, 0.018047577, 0.019914074, 0.039576318, -3.2426347E-4, 0.03845283, 0.049670022, 0.06432235, -0.06008428, -0.080892906, 0.05582591, 0.028310083, -0.090362184, -0.015064784, -0.066851325, -0.012716265, -0.033729102, -0.031012597, 0.0019423878, 0.0750589, 0.01450563, -0.021095097, 0.022074543, 0.0014487508, -0.0042560436, 0.03301075, 0.019492188, 0.006087645, -0.021252045, -0.037356433, -0.012903627, -0.06849498, -0.029681358, -0.013638408, 0.0086266175, 0.030276239, -0.13084114, -0.07070397, -0.008443375, 0.086747505, -0.012094665, -0.04219049, -0.006832875, -0.02894327, -0.05139066, -0.030714685, 0.015877882, 0.0218805, 0.00623874

This section merges everything into one final feature vector we can feed into a model.  
It joins the SBERT embeddings with the TF-IDF features and some simple numeric features (like length + sentiment), then concatenates them into one dense vector called `features`.  Just acknowledging I manually concatenated arrays and used UDFs and a VectorAssembler could have made this cleaner and faster too.

In [0]:

# Combined Feature Set and Output
from datetime import datetime
from pyspark.sql import functions as F, types as T
from pyspark.ml.linalg import Vectors, VectorUDT

emb_out = f"{gold_path}/features_v2/train_text_embeddings_sbert"  # already created

# 1) Read embeddings and join
emb_df = spark.read.format("delta").load(emb_out)
ds = final_tfidf.join(emb_df, on="review_id", how="inner")

# 2) Build ONE 'features' vector without VectorAssembler
to_array = F.udf(lambda v: v.toArray().tolist() if v is not None else None,
                 T.ArrayType(T.DoubleType()))
nums = F.array(
    F.col("review_length_words").cast("double"),
    F.col("review_length_chars").cast("double"),
    F.col("sentiment_pos").cast("double"),
    F.col("sentiment_neu").cast("double"),
    F.col("sentiment_neg").cast("double"),
    F.col("sentiment_compound").cast("double"),
)
concat_arr = F.concat(
    to_array("tfidf_features"),
    F.col("bert_embedding").cast(T.ArrayType(T.DoubleType())),
    nums
)
to_vec = F.udf(lambda a: Vectors.dense(a) if a is not None else None, VectorUDT())
ds_vec = ds.withColumn("features", to_vec(concat_arr))

# 3) Select modeling-ready table
ds_ready = (
    ds_vec.withColumn("label", (F.col("rating") >= 4.0).cast("int"))
          .select(
              "review_id","book_id","user_id","author_id","author_name","title","language_code",
              "rating","date_added","book_review_count","book_avg_rating",
              "features",                          # combined vector
              "tfidf_features","bert_embedding",   # keep parts for debug
              "review_text","clean_text",
              "review_length_words","review_length_chars",
              "sentiment_pos","sentiment_neu","sentiment_neg","sentiment_compound",
              "label"
          )
)

# 4) SAFE WRITE: unique timestamped path + append (no overwrite)
run_id = datetime.now().strftime("%Y%m%d_%H%M%S")
ready_out = f"{gold_path}/features_v2/train_ready_features_{run_id}"

# Optional guard: bail if path already exists (extremely unlikely with timestamp)
try:
    dbutils.fs.ls(ready_out)   # will raise if not exists
    raise RuntimeError(f"Target already exists: {ready_out}")
except Exception as e:
    if "java.io.FileNotFoundException" not in str(e):
        raise  # a real error

(ds_ready.write
    .format("delta")
    .mode("append")           # creates new path if missing
    .save(ready_out))

print("Saved →", ready_out)

# 5) Quick preview of ALL columns (first 10 rows)
display(spark.read.format("delta").load(ready_out).limit(10))


Saved → abfss://lakehouse@goodreadsreviews60300832.dfs.core.windows.net/gold/features_v2/train_ready_features_20251112_071914


review_id book_id user_id author_id author_name title language_code rating date_added book_review_count book_avg_rating features tfidf_features bert_embedding review_text clean_text review_length_words review_length_chars sentiment_pos sentiment_neu sentiment_neg sentiment_compound label 000197dca1e705ed3a3e7be5494e41c7 6185 1e5b241799d306b385fc41908b1c11e1 4191 Emily Bronte Wuthering Heights eng 4.0 2008-09-04 2559 3.5498241500586167 Map(vectorType -> dense, length -> 20390, values -> List(0.07870877925998906, 0.0, 0.0, 0.04728074208570815, 0.0, 0.10652542382930043, 0.0, 0.057323266393540524, 0.0, 0.06254571288474685, 0.06303401820361827, 0.0, 0.1320100461769446, 0.06615189957365993, 0.0, 0.06729409677090643, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.07157556342699874, 0.0, 0.0, 0.07365115075013735, 0.14755772163546588, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.08113023275471891, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.08240083654350858, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.08490763223536739, 0.0, 0.0, 0.08539190251895627, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0919743840720149, 0.0, 0.0, 0.0, 0.0, 0.09230542509165288, 0.0, 0.09259346176204454, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.09640984256569038, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.09728991858700864, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.10281208653827897, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.1103299577213206, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.11277412029854829, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.12237225632330755, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.12577776605659918, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.12714240057831222, 0.12717602587233334, 0.0, 0.0, 0.0, 0.0, 0.0

In [0]:
df = spark.read.format("delta").load(ready_out)
df.printSchema()


root
 |-- review_id: string (nullable = true)
 |-- book_id: string (nullable = true)
 |-- user_id: string (nullable = true)
 |-- author_id: string (nullable = true)
 |-- author_name: string (nullable = true)
 |-- title: string (nullable = true)
 |-- language_code: string (nullable = true)
 |-- rating: double (nullable = true)
 |-- date_added: date (nullable = true)
 |-- book_review_count: long (nullable = true)
 |-- book_avg_rating: double (nullable = true)
 |-- features: vectorudt (nullable = true)
 |-- tfidf_features: vectorudt (nullable = true)
 |-- bert_embedding: array (nullable = true)
 |    |-- element: float (containsNull = true)
 |-- review_text: string (nullable = true)
 |-- clean_text: string (nullable = true)
 |-- review_length_words: integer (nullable = true)
 |-- review_length_chars: integer (nullable = true)
 |-- sentiment_pos: double (nullable = true)
 |-- sentiment_neu: double (nullable = true)
 |-- sentiment_neg: double (nullable = true)
 |-- sentiment_compound: doubl

Plans that i shared and the haters indeed sabotaged me
